In [1]:
%config IPCompleter.greedy=True
import re
import json
import csv
import requests
import re
from collections import defaultdict
from operator import itemgetter
from tqdm import tqdm_notebook as tqdm
from time import time, sleep
import pandas as pd
from qwikidata.sparql import return_sparql_query_results

In [2]:
def json_read(filename):
    with open(filename, 'r') as inf:
        res = json.load(inf)
    return res

def json_dump(obj, filename, ea=False, indent=4):
    with open(filename, 'w') as ouf:
        json.dump(obj, ouf, ensure_ascii=ea, indent=indent)

In [13]:
def get_properties_chain(question_entity_qids, answer_entity_qid, hops=1):
    values_clause = ' '.join(map(lambda s: 'wd:' + s, question_entity_qids))
    select_clause = '?q_entity ?p1 '
    chain_clause_left = '?p1 '
    chain_clause_right = ''
    for i in range(1, hops):
        select_clause += f'?p{i + 1} '
        chain_clause_left += f'[ ?p{i + 1} '
        chain_clause_right += ']'
    query = f'''
    SELECT {select_clause}
    WHERE {{
      VALUES ?q_entity {{ {values_clause} }}
      ?q_entity {chain_clause_left}wd:{answer_entity_qid} {chain_clause_right}.
    }}
    '''
    print(query)
    sleep(0.75)
    response = requests.get('https://query.wikidata.org/sparql', params={'format': 'json', 'query': query})
    to_sleep = 3
    while response.status_code == 429:
        sleep(to_sleep)
        to_sleep += 2
        response = requests.get('https://query.wikidata.org/sparql', params={'format': 'json', 'query': query})
        print('slept')
    result = response.json()
    return result['results']['bindings']

In [ ]:
get_properties_chain([''])

#### Little transformations

In [50]:
parts = ['1_5000', '5001_10000', '10001_14000', '14001_end']

In [61]:
all_matches = []
for part in parts:
    cur_matches = json_read(f'quiz_entities_data_{part}.json')
    all_matches.extend(cur_matches)
edited_matches = []
for match in all_matches:
    a = match['answer']
    m = match['matches']
    if 'text' in match:
        q = match['text']
    else:
        q = match['question']
    if f'({a})' in q:
        q = q.replace(f'({a})', '')
    edited_matches.append({
        'question': q,
        'answer': a,
        'matches': m
    })

In [64]:
json_dump(edited_matches, 'question_matches.json')

In [189]:
question_matches = json_read('question_matches.json')
for item in tqdm(question_matches):
    old_matches = item['matches']
    new_matches = []
    for match in old_matches:
        if match['source'] == 'phrase':
            new_matches.append(match)
    for match in old_matches:
        if match['source'] == 'single':
            new_matches.append(match)
    for match in old_matches:
        if match['source'] == 'fulltext':
            new_matches.append(match)
    assert len(old_matches) == len(new_matches)
    item['matches'] = new_matches

In [191]:
json_dump(question_matches, 'question_matches.json')

#### Loading matches

In [14]:
# build question to matches map
q_matches_list = json_read('question_matches.json')
q_matches = defaultdict(dict)
for qm in q_matches_list:
    q = qm['question']
    m = qm['matches']
    a = qm['answer']
    q_matches[q]['answer'] = a
    q_matches[q]['matches'] = m    

In [193]:
q_answer_labels = json_read('answers_labeling.json')

In [195]:
q_answer_labels = [(k, v) for k, v in q_answer_labels.items()]

In [23]:
que_qids = [e['qid'] for e in q_matches['Какая рок-группа создала хит "Don\'t Cry"?']['matches']]
ans_qid = 'Q11895'

In [25]:
get_properties_chain(que_qids, ans_qid, hops=2)


    SELECT ?q_entity ?p1 ?p2 
    WHERE {
      VALUES ?q_entity { wd:Q1242271 wd:Q1931163 wd:Q1823033 wd:Q2447745 wd:Q1142193 wd:Q16275555 wd:Q896043 wd:Q2575356 wd:Q623470 wd:Q1587210 wd:Q4396798 }
      ?q_entity ?p1 [ ?p2 wd:Q11895 ].
    }
    


[{'q_entity': {'type': 'uri',
   'value': 'http://www.wikidata.org/entity/Q1242271'},
  'p2': {'type': 'uri', 'value': 'http://www.wikidata.org/prop/direct/P175'},
  'p1': {'type': 'uri', 'value': 'http://www.wikidata.org/prop/direct/P155'}},
 {'q_entity': {'type': 'uri',
   'value': 'http://www.wikidata.org/entity/Q1242271'},
  'p2': {'type': 'uri', 'value': 'http://www.wikidata.org/prop/direct/P175'},
  'p1': {'type': 'uri', 'value': 'http://www.wikidata.org/prop/direct/P361'}},
 {'q_entity': {'type': 'uri',
   'value': 'http://www.wikidata.org/entity/Q1242271'},
  'p2': {'type': 'uri',
   'value': 'http://www.wikidata.org/prop/statement/P175'},
  'p1': {'type': 'uri', 'value': 'http://www.wikidata.org/prop/P175'}},
 {'q_entity': {'type': 'uri',
   'value': 'http://www.wikidata.org/entity/Q1242271'},
  'p2': {'type': 'uri', 'value': 'http://www.wikidata.org/prop/direct/P463'},
  'p1': {'type': 'uri', 'value': 'http://www.wikidata.org/prop/direct/P86'}},
 {'q_entity': {'type': 'uri',


#### Searching for chains

In [199]:
chain_results = defaultdict(dict)
cnt = 0
for q, ans_qid in tqdm(q_answer_labels[1300:]):
    chain_results[q]['answer'] = q_matches[q]['answer']
    chain_results[q]['chains'] = []
    que_qids = []
    for q_match in q_matches[q]['matches']:
        que_qids.append(q_match['qid'])
    chain_hop1 = get_properties_chain(que_qids, ans_qid, hops=1)
    chain_hop2 = get_properties_chain(que_qids, ans_qid, hops=2)
    cnt += 2
    if len(chain_hop1) + len(chain_hop2) > 0:
        chain_results[q]['chains'].append(
            {
                1: chain_hop1,
                2: chain_hop2
            }
        )
    if len(chain_results) % 50 == 0:
        json_dump(chain_results, 'chain_results_1301_?.json')

slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slept
slep

#### Exploration

In [216]:
chain_results = json_read('chain_results.json')

In [276]:
cnt = 0
for k, v in chain_results.items():
#     if v['chains'] and v['chains']['1']:
#         if len(v['chains']['1']) == 1:
#             cnt += 1
    if v['chains']:
        cnt += 1

In [277]:
cnt

3194

In [227]:
ans_qids = json_read('answers_labeling.json')

In [239]:
prop_labels = json_read('properties_labels.json')

In [272]:
with open('1hop_chains.txt', 'w') as ouf:
    for q, data in chain_results.items():
        a = data['answer']
        if not data['chains'] or not data['chains']['1']:
            continue
        print(f'Q: {q}', file=ouf)
        print(f'A: {a}\n', file=ouf)
        for i, chain in enumerate(data['chains']['1'], 1):
            que_qid = chain['q_entity']['value'].replace('http://www.wikidata.org/entity/', '')
            for match in q_matches[q]['matches']:
                if match['qid'] == que_qid:
                    que_name = match['name']
            pid = chain['p1']['value'].replace('http://www.wikidata.org/prop/direct/', '')
            p_name = prop_labels[pid]
            print(f'Chain {i}:', file=ouf)
            print(f'{que_name} http://www.wikidata.org/entity/{que_qid}', file=ouf)
            print(f'{p_name} http://www.wikidata.org/prop/direct/{pid}', file=ouf)
            print(f'http://www.wikidata.org/entity/{ans_qids[q]}', file=ouf)
            print(file=ouf)

In [275]:
dataframe_1hop_chains = []
for q, data in chain_results.items():
    a = data['answer']
    if not data['chains'] or not data['chains']['1']:
        continue
    for i, chain in enumerate(data['chains']['1'], 1):
        row = {}
        row['q'] = q
        row['a'] = a
        que_qid = chain['q_entity']['value'].replace('http://www.wikidata.org/entity/', '')
        for match in q_matches[q]['matches']:
            if match['qid'] == que_qid:
                que_name = match['name']
        pid = chain['p1']['value'].replace('http://www.wikidata.org/prop/direct/', '')
        p_name = prop_labels[pid]
        row['qe_name'] = que_name
        row['qe_link'] = f'http://www.wikidata.org/entity/{que_qid}'
        row['prop_name'] = p_name
        row['prop_link'] = f'http://www.wikidata.org/prop/direct/{pid}'
        row['ans_link'] = f'http://www.wikidata.org/entity/{ans_qids[q]}'
        dataframe_1hop_chains.append(row)
df = pd.DataFrame(dataframe_1hop_chains)
df = df[['q', 'a', 'qe_name', 'qe_link', 'prop_name', 'prop_link', 'ans_link']]
df.to_csv('1hop_chains.csv', index=False)

In [285]:
cnt = 1
with open('2hop_chains.txt', 'w') as ouf:
    for q, data in chain_results.items():
        a = data['answer']
        if not data['chains'] or data['chains']['1'] or not data['chains']['2']:
            continue
        if len(data['chains']['2']) > 10:
            continue
        print(f'{cnt}. Q: {q}', file=ouf)
        print(f'A: {a}\n', file=ouf)
        cnt += 1
        for i, chain in enumerate(data['chains']['2'], 1):
            que_qid = chain['q_entity']['value'].replace('http://www.wikidata.org/entity/', '')
            for match in q_matches[q]['matches']:
                if match['qid'] == que_qid:
                    que_name = match['name']
            pid_1 = chain['p1']['value']
            pid_1 = re.sub(r'.*/', '', pid_1)
            p_name_1 = prop_labels[pid_1]
            pid_2 = chain['p2']['value']
            pid_2 = re.sub(r'.*/', '', pid_2)
            p_name_2 = prop_labels[pid_2]
            print(f'Chain {i}:', file=ouf)
            print(f'{que_name} http://www.wikidata.org/entity/{que_qid}', file=ouf)
            print(f'{p_name_1} http://www.wikidata.org/prop/direct/{pid_1}', file=ouf)
            print(f'{p_name_2} http://www.wikidata.org/prop/direct/{pid_2}', file=ouf)
            print(f'http://www.wikidata.org/entity/{ans_qids[q]}', file=ouf)
            print(file=ouf)

In [288]:
dataframe_2hop_chains = []
for q, data in chain_results.items():
    a = data['answer']
    if not data['chains'] or data['chains']['1'] or not data['chains']['2']:
        continue
    if len(data['chains']['2']) > 10:
        continue
    for i, chain in enumerate(data['chains']['2'], 1):
        row = {}
        row['q'] = q
        row['a'] = a
        que_qid = chain['q_entity']['value'].replace('http://www.wikidata.org/entity/', '')
        for match in q_matches[q]['matches']:
            if match['qid'] == que_qid:
                que_name = match['name']
        pid_1 = chain['p1']['value']
        pid_1 = re.sub(r'.*/', '', pid_1)
        p_name_1 = prop_labels[pid_1]
        pid_2 = chain['p2']['value']
        pid_2 = re.sub(r'.*/', '', pid_2)
        p_name_2 = prop_labels[pid_2]
        row['qe_name'] = que_name
        row['qe_link'] = f'http://www.wikidata.org/entity/{que_qid}'
        row['prop_1_name'] = p_name_1
        row['prop_1_link'] = f'http://www.wikidata.org/prop/direct/{pid_1}'
        row['prop_2_name'] = p_name_2
        row['prop_2_link'] = f'http://www.wikidata.org/prop/direct/{pid_2}'
        row['ans_link'] = f'http://www.wikidata.org/entity/{ans_qids[q]}'
        dataframe_2hop_chains.append(row)
df = pd.DataFrame(dataframe_2hop_chains)
df = df[['q', 'a', 'qe_name', 'qe_link', 'prop_1_name', 'prop_1_link', 'prop_2_name', 'prop_2_link', 'ans_link']]
df.to_csv('2hop_chains.csv', index=False)

In [286]:
cnt

1275

In [226]:
q_matches

defaultdict(dict,
            {'Сколько существует законов Ньютона?': {'answer': '3',
              'matches': [{'qid': 'Q935',
                'label': 'Ньютон',
                'score': 12.546672,
                'name': 'Исаак Ньютон',
                'description': 'английский физик, математик и астроном, один из создателей классической физики',
                'ruwiki': 'Ньютон, Исаак',
                'views': 13196,
                'source': 'single'},
               {'qid': 'Q38433',
                'label': 'Законы Ньютона',
                'score': 19.39318,
                'name': 'Законы Ньютона',
                'description': None,
                'ruwiki': 'Законы Ньютона',
                'views': 17927,
                'source': 'fulltext'},
               {'qid': 'Q134465',
                'label': 'Закон тяготения Ньютона',
                'score': 16.19127,
                'name': 'Классическая теория тяготения Ньютона',
                'description': None,
        

In [221]:
next(iter(chain_results.values()))

{'answer': 'Христофор Колумб',
 'chains': {'1': [],
  '2': [{'q_entity': {'type': 'uri',
     'value': 'http://www.wikidata.org/entity/Q668'},
    'p2': {'type': 'uri', 'value': 'http://www.wikidata.org/prop/direct/P138'},
    'p1': {'type': 'uri',
     'value': 'http://www.wikidata.org/prop/direct/P530'}},
   {'q_entity': {'type': 'uri', 'value': 'http://www.wikidata.org/entity/Q30'},
    'p2': {'type': 'uri', 'value': 'http://www.wikidata.org/prop/direct/P61'},
    'p1': {'type': 'uri',
     'value': 'http://www.wikidata.org/prop/direct/P530'}},
   {'q_entity': {'type': 'uri', 'value': 'http://www.wikidata.org/entity/Q30'},
    'p2': {'type': 'uri', 'value': 'http://www.wikidata.org/prop/direct/P138'},
    'p1': {'type': 'uri',
     'value': 'http://www.wikidata.org/prop/direct/P832'}}]}}

In [118]:
list(q_matches.items())[0]

('Сколько существует законов Ньютона?',
 {'answer': '3',
  'matches': [{'qid': 'Q38433',
    'label': 'Законы Ньютона',
    'score': 19.39318,
    'name': 'Законы Ньютона',
    'description': None,
    'ruwiki': 'Законы Ньютона',
    'views': 17927,
    'source': 'fulltext'},
   {'qid': 'Q134465',
    'label': 'Закон тяготения Ньютона',
    'score': 16.19127,
    'name': 'Классическая теория тяготения Ньютона',
    'description': None,
    'ruwiki': 'Классическая теория тяготения Ньютона',
    'views': 4371,
    'source': 'fulltext'},
   {'qid': 'Q122508',
    'label': 'Первый закон Ньютона',
    'score': 16.19127,
    'name': 'Инерция',
    'description': 'Свойства тел сохранять прямолинейное и равномерное движение или состояние покоя',
    'ruwiki': 'Инерция',
    'views': 2553,
    'source': 'fulltext'},
   {'qid': 'Q2902868',
    'label': 'Закон Ньютона Рихмана',
    'score': 16.19127,
    'name': 'Закон Ньютона — Рихмана',
    'description': None,
    'ruwiki': 'Закон Ньютона — Ри

In [128]:
query_string = """
SELECT ?p1 ?p2 
    WHERE {
      wd:Q2621502 ?p1 [ ?p2 wd:Q7322 ].
    }
"""

results = return_sparql_query_results(query_string)

In [127]:
results['results']['bindings']

[]

In [156]:
get_properties_chain(['Q1946569', 'Q5809', 'Q55597694'], 'Q414')


    SELECT ?q_entity ?p1 
    WHERE {
      VALUES ?q_entity { wd:Q1946569 wd:Q5809 wd:Q55597694 }
      ?q_entity ?p1 wd:Q414 .
    }
    
<Response [200]>


[{'q_entity': {'type': 'uri', 'value': 'http://www.wikidata.org/entity/Q5809'},
  'p1': {'type': 'uri', 'value': 'http://www.wikidata.org/prop/direct/P27'}},
 {'q_entity': {'type': 'uri', 'value': 'http://www.wikidata.org/entity/Q5809'},
  'p1': {'type': 'uri', 'value': 'http://www.wikidata.org/prop/direct/P551'}}]

In [134]:
response = requests.get('https://query.wikidata.org/sparql', params={'format': 'json', 'query': query_string})

In [266]:
prop_data_eng = pd.read_csv('properties_data_english.csv', header=0)

In [267]:
prop_data_eng.head()

ID               label                                        description  \
0   P6  head of government  head of the executive power of this town, city...   
1  P10               video  relevant video. For images, use the property P...   
2  P14        traffic sign  graphic symbol describing the item, used at th...   
3  P15           route map            image of route map at Wikimedia Commons   
4  P16      highway system  system (or specific country specific road type...   

                                             aliases     Data type    Count  
0  chancellor, mayor, prime minister, governor, p...  WikibaseItem  22,651   
1           animation, media, gif, trailer (Commons)  CommonsMedia   3,427   
2  highway shield, shield, highway marker, motorw...  CommonsMedia  15,058   
3  schema, highway map, map of route, metro map, ...  CommonsMedia  19,526   
4  transport network, network of routes, part of ...  WikibaseItem  40,109

In [264]:
prop_labels = {}

In [268]:
for index, row in prop_data_eng.iterrows():
    if row['ID'] not in prop_labels:
        prop_labels[row['ID']] = row['label']

In [269]:
json_dump(prop_labels, 'properties_labels.json')

In [3]:
chains = json_read('chain_results.json')

### Compare with annotated question entites

In [39]:
questions_annotations = json_read('question_annotations.json')

In [48]:
questions_annotations

{'Кто пленил князя Игоря?': [0],
 'Где Гарри впервые поцеловал Джинни?': [],
 'Какая повесть есть у А.С. Пушкина?': [4],
 'Чем, согласно русской пословице, красна изба?': [],
 'Как звали придворного органиста английской королевы Елизаветы – по преданию, автора английского гимна?': [],
 'Какой район Нью-Йорка находится на острове?': [1],
 'Какую республику упразнили в СССР в 1924г.?': [1],
 'В какой стране больше всего рек и озёр?': [],
 'Как иначе называют Нидерланды?': [0],
 'Какое любимое варенье Альбуса Дамблдора?': [0],
 'Как летучие мыши определяют положение окружающих предметов?': [1],
 'Как называется комедия Н.В. Гоголя?': [0],
 'Как звали кота Гермионы?': [],
 'Как называется воздушная качка при полётах?': [],
 'В каком городе жили Ромео и Джульетта?': [0],
 'Чем заряжали пушки для уничтожения пехоты?': [1],
 'Какое растение в Библейских приданиях называли «неопалимой купиной»?': [1,
  7],
 'В какой кости лучше всего сохраняется ДНК?': [2],
 'Что буратино пытался найти у караб

In [32]:
question_matches = json_read('q_matches_1_5000.json')

In [42]:
question_matches

[{'question': 'Сколько существует законов Ньютона?',
  'answer': '3',
  'matches': [{'qid': 'Q935',
    'label': 'Ньютон',
    'score': 12.546672,
    'name': 'Исаак Ньютон',
    'description': 'английский физик, математик и астроном, один из создателей классической физики',
    'ruwiki': 'Ньютон, Исаак',
    'views': 13196,
    'source': 'single'},
   {'qid': 'Q38433',
    'label': 'Законы Ньютона',
    'score': 19.39318,
    'name': 'Законы Ньютона',
    'description': None,
    'ruwiki': 'Законы Ньютона',
    'views': 17927,
    'source': 'fulltext'},
   {'qid': 'Q134465',
    'label': 'Закон тяготения Ньютона',
    'score': 16.19127,
    'name': 'Классическая теория тяготения Ньютона',
    'description': None,
    'ruwiki': 'Классическая теория тяготения Ньютона',
    'views': 4371,
    'source': 'fulltext'},
   {'qid': 'Q122508',
    'label': 'Первый закон Ньютона',
    'score': 16.19127,
    'name': 'Инерция',
    'description': 'Свойства тел сохранять прямолинейное и равномерное

In [51]:
qms = {}
for match in question_matches:
    q = match['question']
    ms = [e['qid'] for e in match['matches']]
    if q in questions_annotations and q in chains:
        ids = questions_annotations[q]
        lst = [ms[i] for i in ids]
        qms[q] = lst

In [58]:
dataset = json_read('kbqa_russian_dataset.json')

In [75]:
for entry in dataset:
    q = entry['question_text']
    if q in qms:
        qids = [uri.split('/')[-1] for uri in entry['question_uris']]
        for qid in qids:
            if qid not in qms[q]:
                print(q, qids, qms[q])

Как звали создателя факультета Когтевран (Рейвенкло)? ['Q3187163'] ['Q2500638', 'Q180958']
Как звали дракончика Хагрида? ['Q2658345', 'Q177439'] []
Как звали дракончика Хагрида? ['Q2658345', 'Q177439'] []
Какой цвет имеет краска "индиго"? ['Q422662'] ['Q5967009', 'Q1075']
В какой стране находится гора Эверест? ['Q513'] []
В какой стране обитает кенгуру? ['Q270098'] ['Q5070208']
Какое слово используют итальянцы для обозначения всех видов макаронных изделий? ['Q20019'] ['Q178', 'Q50001']
Как звали жену Одиссея? ['Q47231'] []
В каком регионе России находится один из полюсов холода Северного полушария? ['Q4332408'] ['Q159']
В какой стране основная денежная единица называется БОЛИВАР? ['Q203757'] ['Q747699']
Кто был соавтором С. В. Михалкова в написании текста гимна Советского Союза? ['Q208116', 'Q251918'] ['Q208116']
Как называется мера счета мелких галантерейных и канцелярских предметов, равная 144? ['Q2360980'] ['Q1491689', 'Q875696']
Какую болезнь в России когда-то называли инфлюэнца? [

In [65]:
len(qms)

304

In [66]:
stats = {
    '0': 0,
    '1': [0, 0, 0],
    '2': [0, 0, 0]
}
for q, qids in qms.items():
    chs = chains[q]['chains']
    if chs is None:
        stats['0'] += 1
        continue
    if chs['1']:
        stats['1'][2] += 1
        for ch in chs['1']:
            stats['1'][0] += 1
            qid = ch['q_entity']['value'].split('/')[-1]
            if qid in qids:
                stats['1'][1] += 1
    elif chs['2']:
        stats['2'][2] += 1
        for ch in chs['2']:
            stats['2'][0] += 1
            qid = ch['q_entity']['value'].split('/')[-1]
            if qid in qids:
                stats['2'][1] += 1

In [67]:
stats

{'0': 180, '1': [122, 60, 64], '2': [361, 210, 60]}

In [72]:
17 / 124

0.13709677419354838

In [41]:
chains

{'Кто собирался открыть Индию, а открыл Америку?': {'answer': 'Христофор Колумб',
  'chains': {'1': [],
   '2': [{'q_entity': {'type': 'uri',
      'value': 'http://www.wikidata.org/entity/Q668'},
     'p2': {'type': 'uri',
      'value': 'http://www.wikidata.org/prop/direct/P138'},
     'p1': {'type': 'uri',
      'value': 'http://www.wikidata.org/prop/direct/P530'}},
    {'q_entity': {'type': 'uri',
      'value': 'http://www.wikidata.org/entity/Q30'},
     'p2': {'type': 'uri', 'value': 'http://www.wikidata.org/prop/direct/P61'},
     'p1': {'type': 'uri',
      'value': 'http://www.wikidata.org/prop/direct/P530'}},
    {'q_entity': {'type': 'uri',
      'value': 'http://www.wikidata.org/entity/Q30'},
     'p2': {'type': 'uri',
      'value': 'http://www.wikidata.org/prop/direct/P138'},
     'p1': {'type': 'uri',
      'value': 'http://www.wikidata.org/prop/direct/P832'}}]}},
 'Какое растение называют "дикой розой"?': {'answer': 'Шиповник',
  'chains': {'1': [],
   '2': [{'q_entity'

In [ ]:
for q, v in chains:
    

In [78]:
query = '''
CONSTRUCT {
  wd:Q35869 ?p ?o .
  ?o ?qualifier ?f .
  }
WHERE {
  wd:Q35869 ?p ?o .
  optional {?o ?qualifier ?f .}
  }
'''

In [80]:
resp = requests.get('https://query.wikidata.org/sparql', params={'query': query}, headers={'Accept': 'text/turtle'})

In [82]:
print(resp.text)

@prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix sesame: <http://www.openrdf.org/schema/sesame#> .
@prefix owl: <http://www.w3.org/2002/07/owl#> .
@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .
@prefix fn: <http://www.w3.org/2005/xpath-functions#> .
@prefix foaf: <http://xmlns.com/foaf/0.1/> .
@prefix dc: <http://purl.org/dc/elements/1.1/> .
@prefix hint: <http://www.bigdata.com/queryHints#> .
@prefix bd: <http://www.bigdata.com/rdf#> .
@prefix bds: <http://www.bigdata.com/rdf/search#> .
@prefix psn: <http://www.wikidata.org/prop/statement/value-normalized/> .
@prefix pqn: <http://www.wikidata.org/prop/qualifier/value-normalized/> .
@prefix prn: <http://www.wikidata.org/prop/reference/value-normalized/> .
@prefix mwapi: <https://www.mediawiki.org/ontology#API/> .
@prefix gas: <http://www.bigdata.com/rdf/gas#> .
@prefix wdt: <http://www.wikidata.org/prop/direct/> .
@prefix wdtn: <http://www.wikidata.org/prop